<a href="https://colab.research.google.com/github/abhi271998/Self-Driving-Car-Model-using-CNN-predicting-angle-of-handle-movement/blob/main/Self_Driving_car.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive

drive.mount('/content/MyDrive/')

Drive already mounted at /content/MyDrive/; to attempt to forcibly remount, call drive.mount("/content/MyDrive/", force_remount=True).


In [ ]:
!pip install tqdm

In [ ]:
!unzip '/content/MyDrive/MyDrive/driving_dataset.zip'

Streaming output truncated to the last 5000 lines.
  inflating: driving_dataset/55.jpg  
  inflating: driving_dataset/550.jpg  
  inflating: driving_dataset/5500.jpg  
  inflating: driving_dataset/5501.jpg  
  inflating: driving_dataset/5502.jpg  
  inflating: driving_dataset/5503.jpg  
  inflating: driving_dataset/5504.jpg  
  inflating: driving_dataset/5505.jpg  
  inflating: driving_dataset/5506.jpg  
  inflating: driving_dataset/5507.jpg  
  inflating: driving_dataset/5508.jpg  
  inflating: driving_dataset/5509.jpg  
  inflating: driving_dataset/551.jpg  
  inflating: driving_dataset/5510.jpg  
  inflating: driving_dataset/5511.jpg  
  inflating: driving_dataset/5512.jpg  
  inflating: driving_dataset/5513.jpg  
  inflating: driving_dataset/5514.jpg  
  inflating: driving_dataset/5515.jpg  
  inflating: driving_dataset/5516.jpg  
  inflating: driving_dataset/5517.jpg  
  inflating: driving_dataset/5518.jpg  
  inflating: driving_dataset/5519.jpg  
  inflating: driving_dataset/552.

In [ ]:
folder_path = '/content/driving_dataset/'

In [ ]:
import pandas as pd

In [ ]:
data = pd.read_csv(folder_path + 'data.txt', sep = ' ', header=None)
data.head(1000)

0       1
0      0.jpg    0.00
1      1.jpg    0.00
2      2.jpg    0.00
3      3.jpg    0.00
4      4.jpg    0.00
..       ...     ...
995  995.jpg  162.05
996  996.jpg  158.62
997  997.jpg  155.60
998  998.jpg  150.96
999  999.jpg  146.32

[1000 rows x 2 columns]

In [ ]:
from tensorflow.keras.preprocessing import image
from tensorflow.keras.layers import Dense, Conv2D, Dropout, Flatten
from tensorflow.keras.models import Sequential
import numpy as np
from tqdm import tqdm
from tensorflow.keras.optimizers import Adam
from tensorflow.keras import regularizers

In [ ]:
data=data.values
limit = int(0.8 * data.shape[0])

X_train = data[ :limit, 0]
Y_train = data[ : limit, 1]

X_test = data[limit:, 0]
Y_test = data[limit: , 1]

print(X_train.shape, Y_test.shape)

(36324,) (9082,)


In [ ]:
import random

c = list(zip(X_train, Y_train))
random.shuffle(c)
X_train, Y_train = zip(*c)

c = list(zip(X_test, Y_test))
random.shuffle(c)
X_test, Y_test = zip(*c)

In [ ]:
Train = 0
Test = 0

In [ ]:
def TrainImageGenerator(batch_size):

  global Train
  xb = []
  yb = []

  for ix in range(batch_size):
    img = image.load_img(folder_path + X_train[(Train + ix) % limit], target_size=[66, 200])
    imga = image.img_to_array(img) / 255.0
    xb.append(imga)
    yb.append(Y_train[(Train + ix) % limit] * np.pi / 180.0)
    Train += 1

  return xb, yb

def TestImageGenerator(batch_size):

  global Test
  xb = []
  yb = []
  l = len(X_test)
  for ix in range(batch_size):
    img = image.load_img(folder_path + X_test[(Test + ix) % l], target_size=[66, 200])
    imga = image.img_to_array(img) / 255.0
    xb.append(imga)
    yb.append(Y_test[(Test + ix) % l] * np.pi / 180.0)
    Test += 1
    
  return xb, yb

In [ ]:
model = Sequential()
model.add(Conv2D(24, [5,5], activation='relu', strides=[2,2], kernel_regularizer=regularizers.l2(0.001), input_shape= [66, 200, 3]))
model.add(Conv2D(36, [5,5], activation='relu', strides=[2,2], kernel_regularizer=regularizers.l2(0.001)))
model.add(Conv2D(48, [5,5], activation='relu', strides=[2,2], kernel_regularizer=regularizers.l2(0.001)))
model.add(Conv2D(64, [3,3], activation='relu', kernel_regularizer=regularizers.l2(0.001)))
model.add(Conv2D(64, [3,3], activation='relu', kernel_regularizer=regularizers.l2(0.001)))
model.add(Flatten())
model.add(Dense(128, activation='relu', kernel_regularizer=regularizers.l2(0.001)))
model.add(Dropout(0.2))
model.add(Dense(64, activation='relu', kernel_regularizer=regularizers.l2(0.001)))
model.add(Dropout(0.2))
model.add(Dense(24, activation='relu', kernel_regularizer=regularizers.l2(0.001)))
model.add(Dropout(0.2))
model.add(Dense(1, activation='tanh', kernel_regularizer=regularizers.l2(0.001)))

model.summary()



Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_15 (Conv2D)           (None, 31, 98, 24)        1824      
_________________________________________________________________
conv2d_16 (Conv2D)           (None, 14, 47, 36)        21636     
_________________________________________________________________
conv2d_17 (Conv2D)           (None, 5, 22, 48)         43248     
_________________________________________________________________
conv2d_18 (Conv2D)           (None, 3, 20, 64)         27712     
_________________________________________________________________
conv2d_19 (Conv2D)           (None, 1, 18, 64)         36928     
_________________________________________________________________
flatten_3 (Flatten)          (None, 1152)              0         
_________________________________________________________________
dense_12 (Dense)             (None, 128)              

In [ ]:
 import tensorflow.keras
file_path = '/content/MyDrive/MyDrive/zweights-{val_loss:.4f}.h5'
checkpoint = tensorflow.keras.callbacks.ModelCheckpoint(filepath=file_path, save_best_only=True, save_weights_only=True)  # save_freq=1
callbacks = [checkpoint]



In [ ]:
adam = Adam(0.0001)
model.compile(optimizer=adam, loss='mse', metrics=['accuracy'])

In [ ]:
epochs=5
batch_size = 100
lst = len(X_train)
for epoch in range(epochs):
  for i in tqdm(range(int(lst/ batch_size))):
    xs, ys = TrainImageGenerator(batch_size)
    xs = np.array(xs)
    ys = np.array(ys)
    ys.reshape(-1,1)

    xs1, ys1 = TestImageGenerator(batch_size)
    xs1 = np.array(xs1)
    ys1 = np.array(ys1)
    ys1.reshape(-1,1)

    model.fit(xs, ys, validation_data=(xs1,ys1))




  0%|          | 0/363 [00:00<?, ?it/s]

4/4 [==============================] - 1s 88ms/step - loss: 0.7136 - accuracy: 0.0464 - val_loss: 0.7461 - val_accuracy: 0.0600





  0%|          | 1/363 [00:01<09:22,  1.55s/it]

4/4 [==============================] - 0s 38ms/step - loss: 0.8290 - accuracy: 0.0500 - val_loss: 0.7858 - val_accuracy: 0.0600





  1%|          | 2/363 [00:02<07:44,  1.29s/it]

...




 99%|█████████▉| 361/363 [04:05<00:01,  1.31it/s]

4/4 [==============================] - 0s 42ms/step - loss: 0.1613 - accuracy: 0.0500 - val_loss: 0.3176 - val_accuracy: 0.0000e+00





100%|█████████▉| 362/363 [04:06<00:00,  1.35it/s]

4/4 [==============================] - 0s 40ms/step - loss: 0.1333 - accuracy: 0.0300 - val_loss: 0.1994 - val_accuracy: 0.0200





100%|██████████| 363/363 [04:07<00:00,  1.47it/s]


In [ ]:
## Ys = (100, )... (100, 1)

In [ ]:
epochs=60
batch_size = 100

for epoch in range(epochs):
  for i in tqdm(range(int(lst/ batch_size))):
    xs, ys = TrainImageGenerator(batch_size)
    xs = np.array(xs)
    ys = np.array(ys)
    ys.reshape(-1,1)

    xs1, ys1 = TestImageGenerator(batch_size)
    xs1 = np.array(xs1)
    ys1 = np.array(ys1)
    ys1.reshape(-1,1)

    model.fit(xs, ys, validation_data=(xs1,ys1), callbacks=callbacks)




  0%|          | 0/363 [00:00<?, ?it/s]

4/4 [==============================] - 0s 42ms/step - loss: 0.1203 - accuracy: 0.0500 - val_loss: 0.1966 - val_accuracy: 0.0400





  0%|          | 1/363 [00:00<04:17,  1.40it/s]

4/4 [==============================] - 0s 38ms/step - loss: 0.1186 - accuracy: 0.0400 - val_loss: 0.2272 - val_accuracy: 0.0700





  1%|          | 2/363 [00:01<04:08,  1.45it/s]

...




 72%|███████▏  | 261/363 [04:42<01:53,  1.11s/it]

4/4 [==============================] - 0s 56ms/step - loss: 0.0481 - accuracy: 0.0800 - val_loss: 0.1686 - val_accuracy: 0.0100





 72%|███████▏  | 262/363 [04:43<01:52,  1.11s/it]

4/4 [==============================] - 0s 59ms/step - loss: 0.0583 - accuracy: 0.0800 - val_loss: 0.1937 - val_accuracy: 0.0300





 72%|███████▏  | 263/363 [04:45<01:51,  1.12s/it]